In [3]:
import sys
sys.path.append('../src')
import pandas as pd
import folium
import utils_mistral as utils
import test_mistral as models
import importlib

importlib.reload(models)
importlib.reload(utils)

<module 'utils_mistral' from 'c:\\Users\\g630d\\Documents\\00_Cours\\2024-2025_MIT\\00 Thesis\\Dev\\notebooks\\../src\\utils_mistral.py'>

In [2]:
config = utils.Config(demand = "total_demand")
nodes_df, demand_df, wind_data, solar_data = utils.DataProcessor._import_data(config)
county_data = pd.read_csv(config.file_paths["demand_lat_lon"])

Number of duplicates deleted in nodes_df: 2238


In [10]:
solar_CF = solar_data.values
solar_lat = solar_data.lat.values
solar_lon = solar_data.lon.values

wind_CF = wind_data.values
wind_lat = wind_data.lat.values
wind_lon = wind_data.lon.values

# Step 6: Center the map on New England
us_map = folium.Map(location=[43.0, -71.5], zoom_start=7)

# Define bus type colors
bus_type_colors = {
    1: "blue",
    2: "lightblue",
    3: "red",
    4: "gray"
}

# Plot buses
for _, row in nodes_df.iterrows():
    lat, lon = row["Lat"], -row["Lon"]
    bus_type = row["type"]
    bus_id = row["bus_id"]
    Pd, Qd = row["Pd"], row["Qd"]
    
    tooltip = f"Bus ID: {bus_id}<br>Type: {bus_type}<br>Pd: {Pd} MW<br>Qd: {Qd} MVAr"
    
    folium.CircleMarker(
        location=(lat, lon),
        radius=2,
        color=bus_type_colors.get(bus_type, "black"),
        fill=True,
        fill_color=bus_type_colors.get(bus_type, "black"),
        fill_opacity=0.7,
        tooltip=tooltip
    ).add_to(us_map)

# Plot counties
for _, row in county_data.iterrows():
    lat, lon = row["Lat"], -row["Lon"]
    county_name, state = row["County"], row["State"]
    offshore_wind_allowed = row["offshore-wind-allowed"]
    
    triangle_vertices = [
        (lat, lon),
        (lat + 0.05, lon + 0.05),
        (lat - 0.05, lon + 0.05),
    ]
    
    tooltip = f"County: {county_name}, {state}<br>Offshore Wind Allowed: {offshore_wind_allowed}, Lat: {lat}, Lon: {lon}"
    
    folium.Polygon(
        locations=triangle_vertices,
        color="red",
        fill=True,
        fill_color="red",
        fill_opacity=0.5,
        tooltip=tooltip
    ).add_to(us_map)

# Plot solar and wind data
for i in range(len(solar_lat)):
    folium.CircleMarker(
        location=(solar_lat[i], solar_lon[i]),
        radius=2,
        color="orange",
        fill=True,
        fill_color="orange",
        fill_opacity=0.7,
        tooltip=f"Solar CF: {solar_CF[i]}"
    ).add_to(us_map)

# for i in range(len(wind_lat)):
#     folium.CircleMarker(
#         location=(wind_lat[i], wind_lon[i]),
#         radius=2,
#         color="green",
#         fill=True,
#         fill_color="green",
#         fill_opacity=0.7,
#         tooltip=f"Wind CF: {wind_CF[i]}"
#     ).add_to(us_map)

# Save and visualize the map
# us_map.save("new_england_map.html")
us_map
